#Imports and Installations:


---



In [1]:
!pip install transformer_lens
!pip install einops
!pip install jaxtyping

In [2]:
import os; os.environ['ACCELERATE_DISABLE_RICH'] = "1"
import sys
import einops
import torch
from dataclasses import dataclass
from transformer_lens import HookedTransformer
from transformer_lens.utils import gelu_new, tokenize_and_concatenate
import torch as t
from torch import Tensor
import torch.nn as nn
import numpy as np
import math
from tqdm.notebook import tqdm
from typing import Tuple, List, Optional, Dict
from jaxtyping import Float, Int
from transformers.models.gpt2.tokenization_gpt2_fast import GPT2TokenizerFast
from collections import defaultdict
from rich.table import Table
from rich import print as rprint
import datasets
from torch.utils.data import DataLoader
import wandb
from pathlib import Path
import webbrowser
CUDA_LAUNCH_BLOCKING=1

#config:

---


These Configs are derived from gpt2, I am going to use them as a reference:

In [3]:
@dataclass
class Config:
    d_model: int = 768
    debug: bool = True
    layer_norm_eps: float = 1e-5
    d_vocab: int = 50257
    init_range: float = 0.02
    n_ctx: int = 1024
    d_head: int = 64
    d_mlp: int = 3072
    n_heads: int = 12
    n_layers: int = 12

cfg = Config()
print(cfg)

Config(d_model=768, debug=True, layer_norm_eps=1e-05, d_vocab=50257, init_range=0.02, n_ctx=1024, d_head=64, d_mlp=3072, n_heads=12, n_layers=12)


# Functions definitions:

##Layer Norm:
**Layer normalization** is a crucial component in transformers which consists of multiple layers of **self-attention** mechanisms, the distribution of feature values can shift during training, leading to slow **convergence** or even model **instability**. Layer normalization helps mitigate this by normalizing the inputs to each layer, ensuring that they have **consistent** mean and variance. This stabilizes the learning process, allowing for faster convergence and making it easier to tune hyperparameters.
Also we can see it as a form of **regularization**, enhancing the model's generalization capabilities.

In [4]:
#Layer norm
class LayerNorm(nn.Module):
    def __init__(self, cfg: Config):
        super().__init__()
        self.cfg = cfg
        self.w = nn.Parameter(t.ones(cfg.d_model))
        self.b = nn.Parameter(t.zeros(cfg.d_model))

    def forward(self, residual) :
        mean = torch.mean(residual, dim=-1, keepdim=True)
        var_eps = torch.mean((residual - mean) ** 2, dim=-1, keepdim=True)+ self.cfg.layer_norm_eps
        residual =(residual - mean) / torch.sqrt(var_eps)
        return self.w*residual+self.b



## Embedding


Token embedding functions as a lookup table that translates tokens into corresponding vectors. This mapping is represented as a matrix, denoted as \( W_E \), where each row corresponds to the embedding vector of a specific token. Essentially, \( W_E \) is a collection of these embedding vectors stacked together, providing a structured way to represent the tokens in a numerical format for computational processing in various natural language processing tasks.

In [5]:
#Embed:
class Embed(nn.Module):
    def __init__(self, cfg: Config):
        super().__init__()
        self.cfg = cfg
        self.W_E = nn.Parameter(t.empty((cfg.d_vocab, cfg.d_model)))
        nn.init.normal_(self.W_E, std=self.cfg.init_range)

    def forward(self, tokens):

      return self.W_E[tokens]




##Positional Embedding:
When processing a group of tokens simultaneously, the inherent positional information is lost. To preserve this information, it becomes necessary to embed it separately.

In [6]:
#PosEmbed
class PosEmbed(nn.Module):
    def __init__(self, cfg: Config):
        super().__init__()
        self.cfg = cfg
        self.W_pos = nn.Parameter(t.empty((cfg.n_ctx, cfg.d_model)))
        nn.init.normal_(self.W_pos, std=self.cfg.init_range)

    def forward(self, tokens) :
        batch, seq_len = tokens.shape
        return einops.repeat(self.W_pos[:seq_len], "seq d_model -> batch seq d_model", batch=batch)




##Attention:
My intituion is as follows:
Multiplying *q* (query) and *k* (key) in the context of attention mechanisms serves the purpose of assessing the similarity between words. Importantly, this operation embeds words by utilizing information from other words, essentially defining one word in relation to others. The resulting attention score matrix represents a contextual embedding of words. However, it lacks the detailed information contained within the tokens. To recover this information, the matrix is further processed by multiplying it with *V* (value), which can be conceptualized as a filter applied to *V*(though this analogy is more intuitive in the context of images).

In the transformer architecture, there are distinct embeddings for words, positions, and context. Each of these embeddings is encapsulated within the residual stream in separate subspaces, ensuring that the unique information from each source is preserved. This package of information, comprising word embeddings, positional embeddings, and contextual embeddings, is then passed to the next layer's attention head, where it can be efficiently processed.

There are bunch of explanations on the web, check this [PAPER](https://transformer-circuits.pub/2021/framework/index.html).

transformer-attn-21.png

In [7]:
from torch import einsum
class Attention(nn.Module):

    def __init__(self, cfg: Config):
        super().__init__()
        self.cfg = cfg
        self.W_Q = nn.Parameter(t.empty((cfg.n_heads, cfg.d_model, cfg.d_head)))
        self.W_K = nn.Parameter(t.empty((cfg.n_heads, cfg.d_model, cfg.d_head)))
        self.W_V = nn.Parameter(t.empty((cfg.n_heads, cfg.d_model, cfg.d_head)))
        self.W_O = nn.Parameter(t.empty((cfg.n_heads, cfg.d_head, cfg.d_model)))
        self.b_Q = nn.Parameter(t.zeros((cfg.n_heads, cfg.d_head)))
        self.b_K = nn.Parameter(t.zeros((cfg.n_heads, cfg.d_head)))
        self.b_V = nn.Parameter(t.zeros((cfg.n_heads, cfg.d_head)))
        self.b_O = nn.Parameter(t.zeros((cfg.d_model)))
        nn.init.normal_(self.W_Q, std=self.cfg.init_range)
        nn.init.normal_(self.W_K, std=self.cfg.init_range)
        nn.init.normal_(self.W_V, std=self.cfg.init_range)
        nn.init.normal_(self.W_O, std=self.cfg.init_range)

    def forward(self, normalized_resid_pre) :
        Q=einsum('bpm,nmh->bpnh',normalized_resid_pre,self.W_Q)+self.b_Q
        K=einsum('bpm,nmh->bpnh',normalized_resid_pre,self.W_K)+self.b_K
        V=einsum('bpm,nmh->bpnh',normalized_resid_pre,self.W_V)+self.b_V
        QK=einsum('bpnh,bjnh->bnpj',Q,K)
        scaled_QK=QK/math.sqrt(self.cfg.d_head)
        masked_QK=self.apply_causal_mask(scaled_QK)
        soft_QK=masked_QK.softmax(-1)
        Z=einsum('bnvp,bpnh->bvnh',soft_QK,V)
        o=einsum('bvnh,nhm->bvhm',Z,self.W_O)
        O=einops.reduce(o,'b v h m->b v m','sum')+self.b_O
        return O


    '''
    mask is used to make the model only look at the past (no cheating).
    Even though this step is totally dependent on the task at hand!
    '''
    def apply_causal_mask(self, attn_scores) :

        attn_scores = attn_scores.clone()
        mask = torch.tril(torch.ones_like(attn_scores, dtype=torch.bool))
        attn_scores.masked_fill_(~mask, value=float('-inf'))
        return attn_scores



##MLP:
The Multilayer Perceptron (MLP) component plays a crucial role in retrieving and making sense of this information.
MLP is a memory Mangement unit! It reads information from a subspace,analyze it and check if some feature exist (let's say neuron X activates when the plural feature exists).
So it check features.. as usual.
Also it removes information if it needs storage! example:
MLP with one hidden layer, In some neruon we can find
$$W^{in}_{[:, i]}=- W^{out}_{[i :]}$$
which obviously is erasing.
check this [paper](https://arxiv.org/pdf/2012.14913.pdf ) for more initiuition.

In [8]:
class MLP(nn.Module):
    def __init__(self, cfg: Config):
        super().__init__()
        self.cfg = cfg
        self.W_in = nn.Parameter(t.empty((cfg.d_model, cfg.d_mlp)))
        self.W_out = nn.Parameter(t.empty((cfg.d_mlp, cfg.d_model)))
        self.b_in = nn.Parameter(t.zeros((cfg.d_mlp)))
        self.b_out = nn.Parameter(t.zeros((cfg.d_model)))
        nn.init.normal_(self.W_in, std=self.cfg.init_range)
        nn.init.normal_(self.W_out, std=self.cfg.init_range)

    def forward(self, normalized_resid_mid):

        layer1=einsum('bpd,dm->bpm',normalized_resid_mid,self.W_in)+self.b_in
        non_linear=gelu_new(layer1)
        layer2=einsum('bpm,md ->bpd',non_linear,self.W_out)+self.b_out
        return layer2



##TransformerBlock:


In [9]:
class TransformerBlock(nn.Module):
    def __init__(self, cfg: Config):
        super().__init__()
        self.cfg = cfg
        self.ln1 = LayerNorm(cfg)
        self.attn = Attention(cfg)
        self.ln2 = LayerNorm(cfg)
        self.mlp = MLP(cfg)

    def forward(self, resid_pre):
        lin1=self.ln1(resid_pre)
        attn=self.attn(lin1)+resid_pre
        ln2=self.ln2(attn)
        return self.mlp(ln2)+attn


##Unembed:

In [10]:
class Unembed(nn.Module):
    def __init__(self, cfg):
        super().__init__()
        self.cfg = cfg
        self.W_U = nn.Parameter(t.empty((cfg.d_model, cfg.d_vocab)))
        nn.init.normal_(self.W_U, std=self.cfg.init_range)
        self.b_U = nn.Parameter(t.zeros((cfg.d_vocab), requires_grad=False))

    def forward(self, normalized_resid_final):
        return einsum('bpd,dv->bpv',normalized_resid_final,self.W_U)+self.b_U



## The Transformer!

In [11]:
class OurTransformer(nn.Module):
    def __init__(self, cfg: Config):
        super().__init__()
        self.cfg = cfg
        self.embed = Embed(cfg)
        self.pos_embed = PosEmbed(cfg)
        self.blocks = nn.ModuleList([TransformerBlock(cfg) for _ in range(cfg.n_layers)])
        self.ln_final = LayerNorm(cfg)
        self.unembed = Unembed(cfg)

    def forward(self, tokens):
        wembd=self.embed(tokens)
        pembed=self.pos_embed(tokens)
        residual=wembd+pembed
        for block in self.blocks:
            residual = block(residual)
        normalized=self.ln_final(residual)
        return self.unembed(normalized)


In [12]:
device = t.device("cuda" if t.cuda.is_available() else "cpu")
reference_gpt2 = HookedTransformer.from_pretrained("gpt2-small", fold_ln=False, center_unembed=False, center_writing_weights=False)
OurGPT2 = OurTransformer(Config(debug=False)).to(device)
OurGPT2.load_state_dict(reference_gpt2.state_dict(), strict=False)
test_string = '''In the quiet depths of the cosmos, a brilliant star navigates the vast expanse , illuminating the'''
for i in tqdm(range(100)):
    test_tokens = reference_gpt2.to_tokens(test_string).to(device)
    logits = OurGPT2(test_tokens)
    test_string += reference_gpt2.tokenizer.decode(logits[-1, -1].argmax())

print(test_string)

Using pad_token, but it is not set yet.


Loaded pretrained model gpt2-small into HookedTransformer


  0%|          | 0/100 [00:00<?, ?it/s]

In the quiet depths of the cosmos, a brilliant star navigates the vast expanse , illuminating the sky with its own light.


The star is a bright star, and it is the brightest star in the Milky Way. It is the brightest star in the universe, and it is the brightest star in the universe, and it is the brightest star in the universe, and it is the brightest star in the universe, and it is the brightest star in the universe, and it is the brightest star in the universe, and it is the brightest star in the universe, and it is the


#Resources:

I got many ideas from the following resources:

https://transformer-circuits.pub/2021/framework/index.html

https://colab.research.google.com/drive/1Zl3zSdli_epSfaoQ_HeBCuE6dkGWTowd

https://www.youtube.com/watch?v=KV5gbOmHbjU




#Contact:
[Linkedin](https://www.linkedin.com/in/abderrahmenehamdi/)
[GitHub](https://github.com/a-hamdi)